## Imports

In [5]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from lazypredict.Supervised import LazyClassifier
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.metrics import accuracy_score, f1_score, classification_report
from sklearn.preprocessing import LabelEncoder
from lightgbm import LGBMClassifier
import os
import pickle
import warnings
warnings.filterwarnings("ignore")

## I - Loading the dataset and Quick EDA
You can download the dataset with this link : https://www.kaggle.com/datasets/maharshipandya/-spotify-tracks-dataset

In [6]:
PATH =  os.path.join('..', 'spotify_tracks.csv')

df = pd.read_csv(PATH)
df = df.drop('Unnamed: 0', axis=1) # First we drop this useless column
df.head()

track_id                 artists  \
0  5SuOikwiRyPMVoIQDJUgSV             Gen Hoshino   
1  4qPNDBW1i3p13qLCt0Ki3A            Ben Woodward   
2  1iJBSr7s7jYXzM8EGcbK5b  Ingrid Michaelson;ZAYN   
3  6lfxq3CG4xtTiEg7opyCyx            Kina Grannis   
4  5vjLSffimiIP26QG5WcN2K        Chord Overstreet   

                                          album_name  \
0                                             Comedy   
1                                   Ghost (Acoustic)   
2                                     To Begin Again   
3  Crazy Rich Asians (Original Motion Picture Sou...   
4                                            Hold On   

                   track_name  popularity  duration_ms  explicit  \
0                      Comedy          73       230666     False   
1            Ghost - Acoustic          55       149610     False   
2              To Begin Again          57       210826     False   
3  Can't Help Falling In Love          71       201933     False   
4                     Hold On          82       198853     False   

   danceability  energy  key  loudness  mode  speechiness  acousticness  \
0          0.68    0.46    1     -6.75     0         0.14          0.03   
1          0.42    0.17    1    -17.23     1         0.08          0.92   
2          0.44    0.36    0     -9.73     1         0.06          0.21   
3          0.27    0.06    0    -18.52     1         0.04          0.91   
4          0.62    0.44    2     -9.68     1         0.05          0.47   

   instrumentalness  liveness  valence  tempo  time_signature track_genre  
0              0.00      0.36     0.71  87.92               4    acoustic  
1              0.00      0.10     0.27  77.49               4    acoustic  
2              0.00      0.12     0.12  76.33               4    acoustic  
3              0.00      0.13     0.14 181.74               3    acoustic  
4              0.00      0.08     0.17 119.95               4    acoustic

In [7]:
print(f"Empty values : \n{df.isna().sum()}\n\nDupplicates : {df.duplicated().sum()}\n\nShape : {df.shape}")

Empty values : 
track_id            0
artists             1
album_name          1
track_name          1
popularity          0
duration_ms         0
explicit            0
danceability        0
energy              0
key                 0
loudness            0
mode                0
speechiness         0
acousticness        0
instrumentalness    0
liveness            0
valence             0
tempo               0
time_signature      0
track_genre         0
dtype: int64

Dupplicates : 450

Shape : (114000, 20)


In [8]:
df[df['artists'].isna()]

track_id artists album_name track_name  popularity  \
65900  1kR4gIb7nGxHPI3D2ifs59     NaN        NaN        NaN           0   

       duration_ms  explicit  danceability  energy  key  loudness  mode  \
65900            0     False          0.50    0.58    7     -9.46     0   

       speechiness  acousticness  instrumentalness  liveness  valence  tempo  \
65900         0.06          0.69              0.00      0.07     0.73 138.39   

       time_signature track_genre  
65900               4       k-pop

We can see that the missing values are grouped together on the same line, but the useful information is still there. <br>
We don't need information about the artist, album name or track name in our analysis. So we won't get rid of this row.

In [9]:
df.info() # Evertything look fine here. 

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 114000 entries, 0 to 113999
Data columns (total 20 columns):
 #   Column            Non-Null Count   Dtype  
---  ------            --------------   -----  
 0   track_id          114000 non-null  object 
 1   artists           113999 non-null  object 
 2   album_name        113999 non-null  object 
 3   track_name        113999 non-null  object 
 4   popularity        114000 non-null  int64  
 5   duration_ms       114000 non-null  int64  
 6   explicit          114000 non-null  bool   
 7   danceability      114000 non-null  float64
 8   energy            114000 non-null  float64
 9   key               114000 non-null  int64  
 10  loudness          114000 non-null  float64
 11  mode              114000 non-null  int64  
 12  speechiness       114000 non-null  float64
 13  acousticness      114000 non-null  float64
 14  instrumentalness  114000 non-null  float64
 15  liveness          114000 non-null  float64
 16  valence           11

In [10]:
df['track_genre'].value_counts().sort_values()

track_genre
acoustic       1000
ambient        1000
anime          1000
black-metal    1000
bluegrass      1000
               ... 
trip-hop       1000
turkish        1000
r-n-b          1000
punk           1000
world-music    1000
Name: count, Length: 114, dtype: int64

In [11]:
df['track_genre'].value_counts().describe() # We can see in this dataset that everything music genre is represented by 1000 rows, which is more than enough to train a classification model. 

count    114.00
mean    1000.00
std        0.00
min     1000.00
25%     1000.00
50%     1000.00
75%     1000.00
max     1000.00
Name: count, dtype: float64

In [12]:
df.describe()

popularity  duration_ms  danceability    energy       key  loudness  \
count   114000.00    114000.00     114000.00 114000.00 114000.00 114000.00   
mean        33.24    228029.15          0.57      0.64      5.31     -8.26   
std         22.31    107297.71          0.17      0.25      3.56      5.03   
min          0.00         0.00          0.00      0.00      0.00    -49.53   
25%         17.00    174066.00          0.46      0.47      2.00    -10.01   
50%         35.00    212906.00          0.58      0.69      5.00     -7.00   
75%         50.00    261506.00          0.69      0.85      8.00     -5.00   
max        100.00   5237295.00          0.98      1.00     11.00      4.53   

           mode  speechiness  acousticness  instrumentalness  liveness  \
count 114000.00    114000.00     114000.00         114000.00 114000.00   
mean       0.64         0.08          0.31              0.16      0.21   
std        0.48         0.11          0.33              0.31      0.19   
min        0.00         0.00          0.00              0.00      0.00   
25%        0.00         0.04          0.02              0.00      0.10   
50%        1.00         0.05          0.17              0.00      0.13   
75%        1.00         0.08          0.60              0.05      0.27   
max        1.00         0.96          1.00              1.00      1.00   

        valence     tempo  time_signature  
count 114000.00 114000.00       114000.00  
mean       0.47    122.15            3.90  
std        0.26     29.98            0.43  
min        0.00      0.00            0.00  
25%        0.26     99.22            4.00  
50%        0.46    122.02            4.00  
75%        0.68    140.07            4.00  
max        0.99    243.37            5.00

Data prep : <br>
- First try : with only the genres related to rock music
- Second try : with all genres available in this dataset. 

## II - Modeling : perform a classification model

In order to set up a model, we need ton convert the music genres into integers. 

### A - Data Prep

In [13]:
all_genres = list(df['track_genre'].unique())

In [14]:
# Rock 

target_genre = []

for genre in all_genres:
    if 'rock' in genre:
        target_genre.append(genre)

In [15]:
df_target = df.apply(lambda row : row[df['track_genre'].isin(target_genre)]) # Keeping only rows with genres targeted

label_encoder = LabelEncoder()
df_target['track_genre'] = label_encoder.fit_transform(df_target['track_genre'])

In [16]:
print('We have to keep in mind that :\n')

for i in range(len(df_target['track_genre'].unique())):
    print(target_genre[i], '=', i)

We have to keep in mind that :

alt-rock = 0
hard-rock = 1
j-rock = 2
psych-rock = 3
punk-rock = 4
rock-n-roll = 5
rock = 6
rockabilly = 7


In [17]:
to_keep = ['popularity', 'acousticness', 'duration_ms', 'loudness', 'energy', 'valence', 'instrumentalness', 'danceability', 'liveness', 'tempo', 'track_genre']
df_model = df_target[to_keep].reset_index().drop('index', axis=1)
df_model.head(1)

popularity  acousticness  duration_ms  loudness  energy  valence  \
0          87          0.07       260173     -9.46    0.52     0.34   

   instrumentalness  danceability  liveness  tempo  track_genre  
0              0.15          0.59      0.12  85.01            0

## B - Model

### i - Lazy Classifier

In [18]:
X = df_model.drop('track_genre', axis=1)
y = df_model[['track_genre']]

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, shuffle=True, stratify=y)

In [19]:
clf = LazyClassifier(verbose=-1,ignore_warnings=True, custom_metric=None)
models,predictions = clf.fit(X_train, X_test, y_train, y_test)

  0%|          | 0/29 [00:00<?, ?it/s]

 97%|█████████▋| 28/29 [00:39<00:02,  2.06s/it]

[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000597 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2375
[LightGBM] [Info] Number of data points in the train set: 6400, number of used features: 10
[LightGBM] [Info] Start training from score -2.079442
[LightGBM] [Info] Start training from score -2.079442
[LightGBM] [Info] Start training from score -2.079442
[LightGBM] [Info] Start training from score -2.079442
[LightGBM] [Info] Start training from score -2.079442
[LightGBM] [Info] Start training from score -2.079442
[LightGBM] [Info] Start training from score -2.079442
[LightGBM] [Info] Start training from score -2.079442


100%|██████████| 29/29 [00:40<00:00,  1.41s/it]


In [20]:
models

Accuracy  Balanced Accuracy ROC AUC  F1 Score  \
Model                                                                          
XGBClassifier                      0.52               0.52    None      0.52   
LGBMClassifier                     0.51               0.51    None      0.51   
RandomForestClassifier             0.51               0.51    None      0.51   
ExtraTreesClassifier               0.51               0.51    None      0.50   
SVC                                0.49               0.49    None      0.48   
BaggingClassifier                  0.48               0.48    None      0.48   
NuSVC                              0.46               0.46    None      0.45   
KNeighborsClassifier               0.42               0.43    None      0.43   
AdaBoostClassifier                 0.41               0.41    None      0.40   
QuadraticDiscriminantAnalysis      0.41               0.41    None      0.39   
DecisionTreeClassifier             0.40               0.40    None      0.41   
LabelSpreading                     0.39               0.39    None      0.40   
LabelPropagation                   0.39               0.39    None      0.40   
CalibratedClassifierCV             0.39               0.39    None      0.38   
LinearSVC                          0.39               0.39    None      0.37   
RidgeClassifierCV                  0.39               0.39    None      0.37   
RidgeClassifier                    0.39               0.39    None      0.37   
LogisticRegression                 0.38               0.38    None      0.37   
LinearDiscriminantAnalysis         0.38               0.38    None      0.37   
GaussianNB                         0.36               0.36    None      0.34   
NearestCentroid                    0.35               0.35    None      0.34   
ExtraTreeClassifier                0.35               0.35    None      0.35   
BernoulliNB                        0.32               0.32    None      0.30   
PassiveAggressiveClassifier        0.27               0.27    None      0.24   
Perceptron                         0.25               0.25    None      0.20   
SGDClassifier                      0.22               0.22    None      0.20   
DummyClassifier                    0.12               0.12    None      0.03   

                               Time Taken  
Model                                      
XGBClassifier                        6.88  
LGBMClassifier                       1.12  
RandomForestClassifier               1.85  
ExtraTreesClassifier                 0.92  
SVC                                  5.14  
BaggingClassifier                    0.50  
NuSVC                                4.31  
KNeighborsClassifier                 0.19  
AdaBoostClassifier                   0.79  
QuadraticDiscriminantAnalysis        0.03  
DecisionTreeClassifier               0.09  
LabelSpreading                       3.81  
LabelPropagation                     1.66  
CalibratedClassifierCV              10.11  
LinearSVC                            2.66  
RidgeClassifierCV                    0.05  
RidgeClassifier                      0.05  
LogisticRegression                   0.08  
LinearDiscriminantAnalysis           0.06  
GaussianNB                           0.03  
NearestCentroid                      0.03  
ExtraTreeClassifier                  0.04  
BernoulliNB                          0.04  
PassiveAggressiveClassifier          0.07  
Perceptron                           0.05  
SGDClassifier                        0.25  
DummyClassifier                      0.03

### ii - InterpretML

GRID SEARCH

In [21]:
lgbm = LGBMClassifier()

In [22]:
param_grid = {
    'n_estimators': [50, 100, 150, 200],
    'learning_rate': [0.01, 0.1, 0.2],
    'max_depth': [3, 4, 5, 6]
}

In [23]:
warnings.filterwarnings("ignore")
grid_search = GridSearchCV(estimator=lgbm, param_grid=param_grid, cv=3, scoring='accuracy', verbose=-1, n_jobs=-1)
grid_search.fit(X_train, y_train)

/Users/espechebenjamin/.pyenv/versions/3.10.4/envs/artefact/lib/python3.10/site-packages/sklearn/preprocessing/_label.py:99: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/Users/espechebenjamin/.pyenv/versions/3.10.4/envs/artefact/lib/python3.10/site-packages/sklearn/preprocessing/_label.py:134: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, dtype=self.classes_.dtype, warn=True)
/Users/espechebenjamin/.pyenv/versions/3.10.4/envs/artefact/lib/python3.10/site-packages/sklearn/preprocessing/_label.py:99: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/Users/espechebenjamin/.pyenv/

[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002173 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2371
[LightGBM] [Info] Number of data points in the train set: 4266, number of used features: 10
[LightGBM] [Info] Start training from score -2.078036
[LightGBM] [Info] Start training from score -2.079910
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.005470 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2370
[LightGBM] [Info] Start training from score -2.079910
[LightGBM] [Info] Start training from score -2.078036
[LightGBM] [Info] Number of data points in the train set: 4267, number of used features: 10
[LightGBM] [Info] Start training from score -2.079910
[LightGBM] [Info] Start training from score -2.080145
[LightGBM] [Info] Start training from score -2.078270
[LightGBM] [Info] Start training from sc

/Users/espechebenjamin/.pyenv/versions/3.10.4/envs/artefact/lib/python3.10/site-packages/sklearn/preprocessing/_label.py:99: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/Users/espechebenjamin/.pyenv/versions/3.10.4/envs/artefact/lib/python3.10/site-packages/sklearn/preprocessing/_label.py:134: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, dtype=self.classes_.dtype, warn=True)
/Users/espechebenjamin/.pyenv/versions/3.10.4/envs/artefact/lib/python3.10/site-packages/sklearn/preprocessing/_label.py:99: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/Users/espechebenjamin/.pyenv/

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

/Users/espechebenjamin/.pyenv/versions/3.10.4/envs/artefact/lib/python3.10/site-packages/sklearn/preprocessing/_label.py:99: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/Users/espechebenjamin/.pyenv/versions/3.10.4/envs/artefact/lib/python3.10/site-packages/sklearn/preprocessing/_label.py:134: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, dtype=self.classes_.dtype, warn=True)


...

/Users/espechebenjamin/.pyenv/versions/3.10.4/envs/artefact/lib/python3.10/site-packages/sklearn/preprocessing/_label.py:99: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/Users/espechebenjamin/.pyenv/versions/3.10.4/envs/artefact/lib/python3.10/site-packages/sklearn/preprocessing/_label.py:134: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, dtype=self.classes_.dtype, warn=True)


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

/Users/espechebenjamin/.pyenv/versions/3.10.4/envs/artefact/lib/python3.10/site-packages/sklearn/preprocessing/_label.py:99: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/Users/espechebenjamin/.pyenv/versions/3.10.4/envs/artefact/lib/python3.10/site-packages/sklearn/preprocessing/_label.py:134: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, dtype=self.classes_.dtype, warn=True)


[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000966 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2370
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Info] Number of data points in the train set: 4267, number of used features: 10
[LightGBM] [Info] Start training from score -2.080145
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Info] Start training from score -2.080145
[LightGBM] [Info] Start training from score -2.078270
[LightGBM] [Info] Start training from score -2.080145
[LightGBM] [Info] Start training from score -2.080145
[LightGBM

LGBMClassifier(max_depth=3)

In [24]:
pd.DataFrame(grid_search.cv_results_)

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
0            0.51          0.04             0.04            0.00   
1            1.45          0.33             0.06            0.00   
2            2.52          0.18             0.14            0.05   
3            3.51          0.07             0.19            0.11   
4            1.71          0.31             0.08            0.05   
5            2.10          0.15             0.07            0.00   
6            3.35          0.09             0.14            0.02   
7            5.02          0.20             0.15            0.00   
8            2.01          0.34             0.05            0.00   
9            4.25          0.05             0.11            0.01   
10           7.51          0.62             0.16            0.01   
11          11.98          1.21             0.34            0.12   
12           1.54          0.22             0.07            0.01   
13           3.03          0.22             0.11            0.00   
14           4.39          0.17             0.25            0.10   
15           5.97          0.35             0.43            0.09   
16           1.13          0.22             0.06            0.04   
17           2.95          0.23             0.05            0.00   
18           3.77          0.16             0.10            0.02   
19           5.11          0.42             0.10            0.00   
20           2.37          0.10             0.04            0.00   
21           3.93          0.43             0.07            0.00   
22           6.26          0.17             0.11            0.01   
23           8.14          0.36             0.24            0.11   
24           2.92          0.40             0.05            0.00   
25           5.05          0.42             0.11            0.02   
26           7.46          0.14             0.23            0.05   
27          12.07          1.19             0.30            0.02   
28           2.03          0.19             0.07            0.01   
29           4.92          0.34             0.12            0.00   
30           7.19          0.26             0.22            0.01   
31          10.39          0.86             0.44            0.11   
32           1.66          0.37             0.04            0.02   
33           3.20          0.12             0.05            0.00   
34           4.18          0.10             0.08            0.00   
35          15.32          6.19             0.16            0.07   
36          13.78          2.31             0.06            0.00   
37          19.67          0.44             0.09            0.03   
38          15.22          3.96             0.25            0.06   
39          17.50          0.79             0.30            0.09   
40           5.90          0.58             0.06            0.01   
41           7.45          0.58             0.14            0.05   
42          11.17          0.31             0.27            0.11   
43          16.58          0.77             0.35            0.09   
44           2.62          0.36             0.06            0.01   
45           6.33          1.26             0.12            0.00   
46           9.66          0.25             0.26            0.06   
47           9.12          1.46             0.32            0.06   

   param_learning_rate param_max_depth param_n_estimators  \
0                 0.01               3                 50   
1                 0.01               3                100   
2                 0.01               3                150   
3                 0.01               3                200   
4                 0.01               4                 50   
5                 0.01               4                100   
6                 0.01               4                150   
7                 0.01               4                200   
8                 0.01               5                 50   
9                 0.01               5                100   


In [29]:
best_params = grid_search.best_params_
print("Meilleurs hyperparamètres:", best_params)

Meilleurs hyperparamètres: {'learning_rate': 0.1, 'max_depth': 3, 'n_estimators': 100}


In [25]:
warnings.filterwarnings("ignore")

best_lgbm = LGBMClassifier(**best_params)
best_lgbm.fit(X_train, y_train)

y_pred_train = best_lgbm.predict(X_train)
y_pred_test = best_lgbm.predict(X_test)

accuracy_train = accuracy_score(y_pred_train, y_train)
accuracy_test = accuracy_score(y_pred_test, y_test)

print(f'Précision sur l\'ensemble de train : {accuracy_train * 100:.2f}%')
print(f'Précision sur l\'ensemble de test : {accuracy_test * 100:.2f}%')
#print(classification_report(y_pred, y_test))

Précision sur l'ensemble de train : 66.16%
Précision sur l'ensemble de test : 54.50%


## Save the model

In [27]:
pickle.dump(best_lgbm, open("model_spotify_classifier.pkl", 'wb'))

In [28]:
pickled_model = pickle.load(open("model_spotify_classifier.pkl", 'rb'))
pick_pred = pickled_model.predict(X_test)